# Einops and Einsum
Spent 1 hour 46 min on this section.

Has the benefit of performing operations on tensors using Einstein notation

## Tutorials

In [1]:
import torch
import einops

x = torch.arange(1,21,dtype = torch.float32).reshape((2,5,2))
x

tensor([[[ 1.,  2.],
         [ 3.,  4.],
         [ 5.,  6.],
         [ 7.,  8.],
         [ 9., 10.]],

        [[11., 12.],
         [13., 14.],
         [15., 16.],
         [17., 18.],
         [19., 20.]]])

In [23]:
y = einops.rearrange(x, 'b c h-> c h b')

In [24]:
y

tensor([[[ 1, 11],
         [ 2, 12]],

        [[ 3, 13],
         [ 4, 14]],

        [[ 5, 15],
         [ 6, 16]],

        [[ 7, 17],
         [ 8, 18]],

        [[ 9, 19],
         [10, 20]]])

In [37]:
# composition of axes
z = einops.rearrange(x, 'b h w -> b (h w)')

tensor([[ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10],
        [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]])

In [38]:
z

tensor([[ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10],
        [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]])

In [39]:
z = einops.rearrange(x, 'b h w -> (b h w)')

In [40]:
z

tensor([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18,
        19, 20])

In [54]:
einops.reduce(x, 'b h w -> b h', 'mean')

tensor([[ 1.5000,  3.5000,  5.5000,  7.5000,  9.5000],
        [11.5000, 13.5000, 15.5000, 17.5000, 19.5000]])

In [61]:
# matrix transpose
a = torch.arange(6).reshape(2,3)
torch.einsum('ij -> ji', a)

tensor([[0, 3],
        [1, 4],
        [2, 5]])

In [63]:
# sum
torch.einsum('ij -> ', a)

tensor(15)

In [66]:
# column sum
torch.einsum('ij -> j', a)

tensor([3, 5, 7])

In [67]:
# row sum
torch.einsum('ij -> i',a)

tensor([ 3, 12])

In [70]:
# matrix vector multiplication
b = torch.arange(3, dtype=torch.long)
torch.einsum('ij, j -> i' , [a, b])

tensor([ 5, 14])

In [71]:
# matrix-matrix multiplication
b = torch.arange(15).reshape(3,5)
torch.einsum('ij,jk -> ik', [a,b])

tensor([[ 25,  28,  31,  34,  37],
        [ 70,  82,  94, 106, 118]])

In [75]:
# dot product
a = torch.arange(3)
b = torch.arange(3,6)
torch.einsum('i, i -> ', [a,b])

tensor(14)

In [77]:
# matrix dot product
a = torch.arange(6).reshape(2,3)
b = torch.arange(6,12).reshape(2,3)
torch.einsum('ij, ij ->', [a,b])

tensor(145)

In [78]:
# hadamard product
a = torch.arange(6).reshape(2,3)
b = torch.arange(6,12).reshape(2,3)
torch.einsum('ij, ij -> ij', [a,b])

tensor([[ 0,  7, 16],
        [27, 40, 55]])

In [79]:
# outer product
a = torch.arange(3)
b = torch.arange(3,7)
torch.einsum('i,j -> ij', [a,b])

tensor([[ 0,  0,  0,  0],
        [ 3,  4,  5,  6],
        [ 6,  8, 10, 12]])

In [80]:
# batch matrix multiplication
a = torch.randn(3,2,5)
b = torch.randn(3,5,3)
torch.einsum('ijk, ikl -> ijl', [a,b])

tensor([[[-3.3313,  0.1170,  0.6832],
         [ 0.6430,  0.2728,  0.5040]],

        [[-1.9287,  2.0800, -0.4331],
         [-0.8169,  1.8804,  1.2744]],

        [[ 1.3175, -2.2468,  3.0225],
         [ 1.0122, -0.5253,  1.9135]]])

## Exercises

In [2]:
import numpy as np
from fancy_einsum import einsum
from einops import reduce, rearrange, repeat
from typing import Union, Optional, Callable
import torch as t
import torchvision
import utils

arr = np.load("numbers.npy")

In [3]:
arr.shape

(6, 3, 150, 150)

In [8]:
def d(x):
    utils.display_array_as_img(x)


In [26]:
d(einops.rearrange(arr, 'i j k l -> j k (i l)'))

In [27]:
d(einops.repeat(arr[0], 'i j k -> i (2 j) k'))

In [47]:
oneStep = einops.repeat(arr[0:2], 'i j k l -> j (i k) l')
d(einops.repeat(oneStep, 'i j k -> i j (2 k)'))

In [55]:
d(einops.repeat(arr[0], 'i j k -> i (j repeat) k', repeat = 2))

I had to look the bottom one up. Didn't realize that these were just the different channels of the image

In [73]:
d(rearrange(arr[0], "c h w -> h (c w)"))

(This is cheating)

In [100]:
from math import comb


top = t.tensor(einops.repeat(arr[0:3], 'i j k l -> j k (i l)'))
bottom = t.tensor(einops.repeat(arr[3:6], 'i j k l -> j k (i l)'))
combined = torch.stack([top, bottom], 0)
d(rearrange(combined, 'i j k l -> j (i k) l'))

In [102]:
d(einops.reduce(arr, 'i j k l -> k (i l)', 'max'))

In [106]:
d(einops.reduce(arr.astype(np.float32), 'i j k l -> k (i l)', 'mean').astype(int))

In [112]:
d(einops.reduce(arr.astype(float), 'i j k l -> k l', 'min'))

This one I looked at the answer. Shouldn't have, whoops. If I had just played around with it a bit more I would've gotten it.

In [119]:
sideBySide = einops.rearrange(arr[0:2], 'i j k l -> j k ( i l)')

d(rearrange(sideBySide, 'c (h2 h) w -> c h (h2 w)', h2 = 2))

In [120]:
d(rearrange(arr[1], 'i j k -> i k j'))

In [122]:
d(rearrange(arr, '(b1 b2) i j k -> i (b1 k) (b2 j)', b1 = 2))

In [125]:
arr1 = rearrange(arr, "(b1 b2) c h w -> c (b1 h) (b2 w)", b1=2)
d(reduce(arr1, 'i (j 2) (k 2) -> i j k', 'max'))

In [145]:
arr1 = reduce(arr, 'i j (k 10) (l 10) -> i j k l', 'max')
arr2 = repeat(arr1, 'i j k l -> i j (10 k) (10 l)')
d(rearrange(arr2, '(d1 d2) i j k -> i (d1 j) (d2 k)', d1 = 2))

In [165]:
from fancy_einsum import einsum
def einsum_trace(mat: np.ndarray):
    """
    Returns the same as `np.trace`.
    """
    return einsum("i i", mat)

def einsum_mv(mat: np.ndarray, vec: np.ndarray):
    """
    Returns the same as `np.matmul`, when `mat` is a 2D array and `vec` is 1D.
    """
    return einsum("i j, j -> i ", mat,vec)

def einsum_mm(mat1: np.ndarray, mat2: np.ndarray):
    """
    Returns the same as `np.matmul`, when `mat1` and `mat2` are both 2D arrays.
    """
    return einsum("i j, j k -> i k", mat1, mat2)

def einsum_inner(vec1, vec2):
    """
    Returns the same as `np.inner`.
    """
    return einsum("i, i", vec1, vec2)

def einsum_outer(vec1, vec2):
    """
    Returns the same as `np.outer`.
    """
    return einsum("i, j -> i j", vec1, vec2)

utils.test_einsum_trace(einsum_trace)
utils.test_einsum_mv(einsum_mv)
utils.test_einsum_mm(einsum_mm)
utils.test_einsum_inner(einsum_inner)
utils.test_einsum_outer(einsum_outer)

# Array Strides

Spent one hour on this, I have a good understanding of how it works and why it is important. I had to look up the answer for the matrix problem, so I'll proably come back to revisit this

Rought idea: Strides can create views of arrays by specifying how much memory to jump across to get to the next dimension

The nth element in a stride is the number of elements in continguous memory we need to skip over to move on index position in the nth dimension

In [167]:
test_input = t.tensor(
    [[0, 1, 2, 3, 4], 
    [5, 6, 7, 8, 9], 
    [10, 11, 12, 13, 14], 
    [15, 16, 17, 18, 19]], dtype=t.float
)

In [182]:
import torch as t
from collections import namedtuple

TestCase = namedtuple("TestCase", ["output", "size", "stride"])

test_cases = [
    TestCase(
        output=t.tensor([0, 1, 2, 3]), 
        size=(4,), 
        stride=(1,)),
    TestCase(
        output=t.tensor([0, 1, 2, 3, 4]), 
        size=(5,), 
        stride=(1,)),
    TestCase(
        output=t.tensor([0, 5, 10, 15]), 
        size=(4,), 
        stride=(5,)),
    TestCase(
        output=t.tensor([[0, 1, 2], [5, 6, 7]]), 
        size=(2,3), 
        stride=(5,1)),
    TestCase(
        output=t.tensor([[0, 1, 2], [10, 11, 12]]), 
        size=(2,3), 
        stride=(10,1)),
    TestCase(
        output=t.tensor([[0, 0, 0], [11, 11, 11]]), 
        size=(2,3),
        stride=(11,0)),    
    TestCase(
        output=t.tensor([0, 6, 12, 18]), 
        size=(4,), 
        stride=(6,)),
    TestCase(
        output=t.tensor([[[0, 1, 2]], [[9, 10, 11]]]), 
        size=(2,1,3), 
        stride=(9,0,1)),
    TestCase(
        output=t.tensor([[[[0, 1], [2, 3]], [[4, 5], [6, 7]]], [[[12, 13], [14, 15]], [[16, 17], [18, 19]]]]),
        size=(2,2,2,2),
        stride=(12,4,2,1))
]
for (i, case) in enumerate(test_cases):
    if (case.size is None) or (case.stride is None):
        print(f"Test {i} failed: attempt missing.")
    else:
        actual = test_input.as_strided(size=case.size, stride=case.stride)
        if (case.output != actual).any():
            print(f"Test {i} failed:")
            print(f"Expected: {case.output}")
            print(f"Actual: {actual}")
        else:
            print(f"Test {i} passed!")

Test 0 passed!
Test 1 passed!
Test 2 passed!
Test 3 passed!
Test 4 passed!
Test 5 passed!
Test 6 passed!
Test 7 passed!
Test 8 passed!


## Intermediate

In [185]:
def as_strided_trace(mat: t.Tensor) -> t.Tensor:
    '''
    Returns the same as `torch.trace`, using only `as_strided` and `sum` methods.
    '''
    newT = t.as_strided(mat, (mat.shape[1],), (mat.shape[1]+1,)).sum()
    return newT

utils.test_trace(as_strided_trace)

In [194]:
def as_strided_mv(mat: t.Tensor, vec: t.Tensor) -> t.Tensor:
    '''
    Returns the same as `torch.matmul`, using only `as_strided` and `sum` methods.
    '''
    vecLength = vec.shape[0]
    matrixHeight = mat.shape[0]
    largerVector = t.as_strided(vec, mat.shape, (0,vec.stride()[0])) # i think i get this

    expanded_product = mat * largerVector
    # print(mat)
    # print(largerVector)
    # print(expanded_product)
    return expanded_product.sum(dim = 1)
    



utils.test_mv(as_strided_mv)
utils.test_mv2(as_strided_mv)

In [200]:
def as_strided_mm(matA: t.Tensor, matB: t.Tensor) -> t.Tensor:
    '''
    Returns the same as `torch.matmul`, using only `as_strided` and `sum` methods.
    '''

    sAX, sAY = matA.stride()
    sBX, sBY = matB.stride()

    i = matA.shape[0]
    j = matA.shape[1]
    k = matB.shape[1]

    largerMatA = t.as_strided(matA, (i,j,k), (sAX,sAY,0))
    largerMatB = t.as_strided(matB, (i,j,k), (0,sBX, sBY))
    product = largerMatA * largerMatB
    return product.sum(dim = 1)
    

utils.test_mm(as_strided_mm)
utils.test_mm2(as_strided_mm)

# Convolutional Neural Networks

Spent 2 hours and 47 minutes on this section. Banged my head against a lot of the problems, but was mostly worth it

If the following code is genuinely right, i'M GOING TO BE ENTHRALLED. used NO HITS, simply stared at it for 30 minutes to figure it out. WOOOOOOOOO!

In [26]:
import torch as t
import utils
def conv1d_minimal(x: t.Tensor, weights: t.Tensor) -> t.Tensor:
    '''Like torch's conv1d using bias=False and all other keyword arguments left at their default values.

    x: shape (batch, in_channels, width)
    weights: shape (out_channels, in_channels, kernel_width)

    Returns: shape (batch, out_channels, output_width)
    '''

    batch = x.shape[0]
    in_channels = x.shape[1]
    width = x.shape[2]
    out_channels = weights.shape[0]
    kernel_width = weights.shape[2]
    output_width = width - kernel_width + 1

    image_size = in_channels * width # (treated it as one big image)

    x_kernel = t.as_strided(x,
    (output_width, batch, in_channels, kernel_width),  
    (1, in_channels * width, width, 1))

    # for each weight in kernel of shape (in_channels, kernel_width)

    # print(x.shape)
    # print(weights.shape)

    eachKernel = []
    for kernel_weight in range(weights.shape[0]):
        kernel = weights[kernel_weight]
        resultant = x_kernel * kernel
        # print(resultant.shape)
        # resultant is currently size (output_width, batch, in_channels, kernel_width)
        resultant = resultant.sum(3)
        resultant = resultant.sum(2)
        # print("resultant shape post adds:")
        # print(resultant.shape)
        resultant = einops.rearrange(resultant, 'o b -> b 1 o')
        # print(resultant.shape)
        # resultant needs to go to batch, 1, output_width
        eachKernel.append(resultant)

    # concatenate all resultants --> batch, out_channels, output_width
    return torch.cat(eachKernel, dim = 1)

utils.test_conv1d_minimal(conv1d_minimal)

For the conv2d, this one was heavily influenced by my reading through the answer key of the 1-D solution. I don't quite get how the einsum part of it is multiplying everything together to do what my intuition showed me as doing above, but I'll throw it down here with the knowledge that it *does*. It just feels like black magic right now, magically multplying the right things together and summing the right things together.

In [25]:
import fancy_einsum as einsum
def conv2d_minimal(x: t.Tensor, weights: t.Tensor) -> t.Tensor:
    '''Like torch's conv2d using bias=False and all other keyword arguments left at their default values.

    x: shape (batch, in_channels, height, width)
    weights: shape (out_channels, in_channels, kernel_height, kernel_width)

    Returns: shape (batch, out_channels, output_height, output_width)
    '''
    batch, in_channels, height, width = x.shape
    out_channels, in_channels, kernel_height, kernel_width = weights.shape

    output_height = height - kernel_height + 1
    output_width = width - kernel_width + 1

    xB, xIC, xH, xW = x.stride()

    size = (batch, in_channels, output_height, output_width, kernel_height, kernel_width)
    strides = (xB, xIC, xH, xW, xH, xW)
    x_strided = t.as_strided(x, size, strides)

    # einsum doing black magic here...
    result = einsum.einsum('batch in_channels output_height output_width kernel_height kernel_width, out_channels in_channels kernel_height kernel_width -> batch out_channels output_height output_width', x_strided, weights)
    return result

utils.test_conv2d_minimal(conv2d_minimal)

Padding was pretty straightforward

In [30]:
def pad1d(x: t.Tensor, left: int, right: int, pad_value: float) -> t.Tensor:
    '''Return a new tensor with padding applied to the edges.

    x: shape (batch, in_channels, width), dtype float32

    Return: shape (batch, in_channels, left + right + width)
    '''
    
    ## cheating with pytorch? t.nn.functional.pad(x,(left,right), value = pad_value)
    X, Y, Z = x.shape

    tens = x.new_full((X, Y, left + Z + right), pad_value)
    tens[..., left:left + Z] = x
    return tens

utils.test_pad1d(pad1d)
utils.test_pad1d_multi_channel(pad1d)

In [34]:
def pad2d(x: t.Tensor, left: int, right: int, top: int, bottom: int, pad_value: float) -> t.Tensor:
    '''Return a new tensor with padding applied to the edges.

    x: shape (batch, in_channels, height, width), dtype float32

    Return: shape (batch, in_channels, top + height + bottom, left + width + right)
    '''
    B, I, H, W = x.shape

    tens = x.new_full((B, I, top + H + bottom, left + W + right), pad_value)
    tens[...,top:top+H, left:left + W] = x
    return tens


utils.test_pad2d(pad2d)
utils.test_pad2d_multi_channel(pad2d)

## Implementing conv1d and conv2d

(again, a lot of these einsum operations looking crazy... i don't know why they work, just that they do)

In [44]:
import math
def conv1d(x, weights, stride: int = 1, padding: int = 0) -> t.Tensor:
    '''Like torch's conv1d using bias=False.

    x: shape (batch, in_channels, width)
    weights: shape (out_channels, in_channels, kernel_width)

    Returns: shape (batch, out_channels, output_width)
    '''

    new_x = pad1d(x, padding, padding, 0)

    batch, in_channels, width = x.shape
    out_channels, in_channels, kernel_width = weights.shape
    xB, xIB, xW = new_x.stride()

    output_width = 1 + (width + 2 * padding - kernel_width) // stride
    size = (batch, in_channels, output_width, kernel_width)
    strides = (xB, xIB, xW * stride, xW)
    new_x = t.as_strided(new_x, size, strides)

    return einsum.einsum('batch in_channels output_width kernel_width, out_channels in_channels kernel_width -> batch out_channels output_width', new_x, weights)

utils.test_conv1d(conv1d)

In [46]:
from typing import Union
IntOrPair = Union[int, tuple[int, int]]
Pair = tuple[int, int]

def force_pair(v: IntOrPair) -> Pair:
    '''Convert v to a pair of int, if it isn't already.'''
    if isinstance(v, tuple):
        if len(v) != 2:
            raise ValueError(v)
        return (int(v[0]), int(v[1]))
    elif isinstance(v, int):
        return (v, v)
    raise ValueError(v)

# Examples of how this function can be used:
#       force_pair((1, 2))     ->  (1, 2)
#       force_pair(2)          ->  (2, 2)
#       force_pair((1, 2, 3))  ->  ValueError

In [75]:
def conv2d(x, weights, stride: IntOrPair = 1, padding: IntOrPair = 0) -> t.Tensor:
    '''Like torch's conv2d using bias=False

    x: shape (batch, in_channels, height, width)
    weights: shape (out_channels, in_channels, kernel_height, kernel_width)


    Returns: shape (batch, out_channels, output_height, output_width)
    '''

   
    new_x = pad2d(x, padding[1], padding[1], padding[0], padding[0], 0)

    batch, in_channels, height, width = x.shape
    out_channels, in_channels, kernel_height, kernel_width = weights.shape
    xB, xIB, xH, xW = new_x.stride()


    output_width = 1 + (width + 2 * padding[1] - kernel_width) // stride[1]
    output_height = 1 + (height + 2 * padding[0] - kernel_height) // stride[0]
    size = (batch, in_channels, output_height, output_width, kernel_height, kernel_width)
    strides = (xB, xIB, xH * stride[0], xW * stride[1],  xH, xW)
    new_x = t.as_strided(new_x, size, strides)

    return einsum.einsum('batch in_channels output_height output_width kernel_height kernel_width, out_channels in_channels kernel_height kernel_width -> batch out_channels output_height output_width ', new_x, weights)


utils.test_conv2d(conv2d)

In [101]:
from typing import Optional

def maxpool2d(x: t.Tensor, kernel_size: IntOrPair, stride: Optional[IntOrPair] = None, padding: IntOrPair = 0
) -> t.Tensor:
    '''Like PyTorch's maxpool2d.

    x: shape (batch, channels, height, width)
    stride: if None, should be equal to the kernel size

    Return: (batch, channels, out_height, output_width)
    '''
    if stride == None:
        stride = kernel_size

    new_x = pad2d(x, padding[1], padding[1], padding[0], padding[0], -99999999999)

    batch, in_channels, height, width = x.shape
    kernel_height = kernel_size[0]
    kernel_width = kernel_size[1]

    xB, xIB, xH, xW = new_x.stride()


    output_width = 1 + (width + 2 * padding[1] - kernel_width) // stride[1]
    output_height = 1 + (height + 2 * padding[0] - kernel_height) // stride[0]
    size = (batch, in_channels, output_height, output_width, kernel_height, kernel_width)
    strides = (xB, xIB, xH * stride[0], xW * stride[1],  xH, xW)
    new_x = t.as_strided(new_x, size, strides)

    new_x = t.amax(new_x, 5)
    new_x = t.amax(new_x, 4)
    return new_x

utils.test_maxpool2d(maxpool2d)